# AFL 2 - Hagen Kwik

## Imports

In [1]:
# library for mathematical functions and data preprocessing such as table, etc
import pandas as pd
import seaborn as sns

# Library for visualizing data
import matplotlib.pyplot as plt

# Library for machine learning functions/algorithms
from sklearn.model_selection import train_test_split
from sklearn.metrics import confusion_matrix, accuracy_score
from sklearn.preprocessing import LabelEncoder
from sklearn.ensemble import RandomForestClassifier

## Load Data

In [3]:
url = 'lending_club_loan_two.csv'
url_info = 'lending_club_info.csv'
df = pd.read_csv(url)
df_info = pd.read_csv(url_info)
df.head()

loan_amnt        term  int_rate  installment grade sub_grade  \
0    10000.0   36 months     11.44       329.48     B        B4   
1     8000.0   36 months     11.99       265.68     B        B5   
2    15600.0   36 months     10.49       506.97     B        B3   
3     7200.0   36 months      6.49       220.65     A        A2   
4    24375.0   60 months     17.27       609.33     C        C5   

                 emp_title emp_length home_ownership  annual_inc  ...  \
0                Marketing  10+ years           RENT    117000.0  ...   
1          Credit analyst     4 years       MORTGAGE     65000.0  ...   
2             Statistician   < 1 year           RENT     43057.0  ...   
3          Client Advocate    6 years           RENT     54000.0  ...   
4  Destiny Management Inc.    9 years       MORTGAGE     55000.0  ...   

  open_acc pub_rec revol_bal revol_util total_acc  initial_list_status  \
0     16.0     0.0   36369.0       41.8      25.0                    w   
1     17.0     0.0   20131.0       53.3      27.0                    f   
2     13.0     0.0   11987.0       92.2      26.0                    f   
3      6.0     0.0    5472.0       21.5      13.0                    f   
4     13.0     0.0   24584.0       69.8      43.0                    f   

  application_type  mort_acc  pub_rec_bankruptcies  \
0       INDIVIDUAL       0.0                   0.0   
1       INDIVIDUAL       3.0                   0.0   
2       INDIVIDUAL       0.0                   0.0   
3       INDIVIDUAL       0.0                   0.0   
4       INDIVIDUAL       1.0                   0.0   

                                           address  
0     0174 Michelle Gateway\nMendozaberg, OK 22690  
1  1076 Carney Fort Apt. 347\nLoganmouth, SD 05113  
2  87025 Mark Dale Apt. 269\nNew Sabrina, WV 05113  
3            823 Reid Ford\nDelacruzside, MA 00813  
4             679 Luna Roads\nGreggshire, VA 11650  

[5 rows x 27 columns]

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 396030 entries, 0 to 396029
Data columns (total 27 columns):
 #   Column                Non-Null Count   Dtype  
---  ------                --------------   -----  
 0   loan_amnt             396030 non-null  float64
 1   term                  396030 non-null  object 
 2   int_rate              396030 non-null  float64
 3   installment           396030 non-null  float64
 4   grade                 396030 non-null  object 
 5   sub_grade             396030 non-null  object 
 6   emp_title             373103 non-null  object 
 7   emp_length            377729 non-null  object 
 8   home_ownership        396030 non-null  object 
 9   annual_inc            396030 non-null  float64
 10  verification_status   396030 non-null  object 
 11  issue_d               396030 non-null  object 
 12  loan_status           396030 non-null  object 
 13  purpose               396030 non-null  object 
 14  title                 394274 non-null  object 
 15  

In [5]:
columns_to_drop = ['emp_title', 'address', 'issue_d', 'title', 'earliest_cr_line', 'initial_list_status', 'grade', 'sub_grade']

df = df.drop(columns=columns_to_drop)

In [6]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 396030 entries, 0 to 396029
Data columns (total 19 columns):
 #   Column                Non-Null Count   Dtype  
---  ------                --------------   -----  
 0   loan_amnt             396030 non-null  float64
 1   term                  396030 non-null  object 
 2   int_rate              396030 non-null  float64
 3   installment           396030 non-null  float64
 4   emp_length            377729 non-null  object 
 5   home_ownership        396030 non-null  object 
 6   annual_inc            396030 non-null  float64
 7   verification_status   396030 non-null  object 
 8   loan_status           396030 non-null  object 
 9   purpose               396030 non-null  object 
 10  dti                   396030 non-null  float64
 11  open_acc              396030 non-null  float64
 12  pub_rec               396030 non-null  float64
 13  revol_bal             396030 non-null  float64
 14  revol_util            395754 non-null  float64
 15  

In [7]:
df.isna().sum()

loan_amnt                   0
term                        0
int_rate                    0
installment                 0
emp_length              18301
home_ownership              0
annual_inc                  0
verification_status         0
loan_status                 0
purpose                     0
dti                         0
open_acc                    0
pub_rec                     0
revol_bal                   0
revol_util                276
total_acc                   0
application_type            0
mort_acc                37795
pub_rec_bankruptcies      535
dtype: int64

In [124]:
# Check which column needs fixing
for column in df.columns:
    unique_values = df[column].unique()
    print(f"Unique values in '{column}':")
    print(unique_values)
    print()

Unique values in 'loan_amnt':
[10000.  8000. 15600. ... 36275. 36475.   725.]

Unique values in 'term':
[' 36 months' ' 60 months']

Unique values in 'int_rate':
[11.44 11.99 10.49  6.49 17.27 13.33  5.32 11.14 10.99 16.29 13.11 14.64
  9.17 12.29  6.62  8.39 21.98  7.9   6.97  6.99 15.61 11.36 13.35 12.12
  9.99  8.19 18.75  6.03 14.99 16.78 13.67 13.98 16.99 19.91 17.86 21.49
 12.99 18.54  7.89 17.1  18.25 11.67  6.24  8.18 12.35 14.16 17.56 18.55
 22.15 10.39 15.99 16.07 24.99  9.67 19.19 21.   12.69 10.74  6.68 19.22
 11.49 16.55 19.97 24.7  13.49 18.24 16.49 25.78 25.83 18.64  7.51 13.99
 15.22 15.31  7.69 19.53 10.16  7.62  9.75 13.68 15.88 14.65  6.92 23.83
 10.75 18.49 20.31 17.57 27.31 19.99 22.99 12.59 10.37 14.33 13.53 22.45
 24.5  17.99  9.16 12.49 11.55 17.76 28.99 23.1  20.49 22.7  10.15  6.89
 19.52  8.9  14.3   9.49 25.99 24.08 13.05 14.98 16.59 11.26 25.89 14.48
 21.99 23.99  5.99 14.47 11.53  8.67  8.59 10.64 23.28 25.44  9.71 16.2
 19.24 24.11 15.8  15.96 14.49 18.99

In [9]:

columns_with_nan = df.columns[df.isnull().any()].tolist()

# Select rows where NaN values are present in any of the specified columns
nan_data_table = df[df[columns_with_nan].isnull().any(axis=1)]

nan_data_table


loan_amnt        term  int_rate  installment emp_length  \
22         4200.0   36 months      6.99       129.67    5 years   
25         6000.0   36 months     11.36       197.47    2 years   
32         3000.0   36 months      6.03        91.31     1 year   
35         5375.0   36 months     13.11       181.39        NaN   
36         3250.0   36 months     16.78       115.52        NaN   
...           ...         ...       ...          ...        ...   
395999    11125.0   36 months     24.11       437.11        NaN   
396015     4000.0   36 months      9.16       127.50        NaN   
396016     3000.0   36 months      5.42        90.48  10+ years   
396021     3200.0   36 months      5.42        96.52  10+ years   
396029     2000.0   36 months     13.61        67.98  10+ years   

       home_ownership  annual_inc verification_status  loan_status  \
22                OWN    24000.00        Not Verified   Fully Paid   
25               RENT    46680.00        Not Verified  Charged Off   
32                OWN    64000.00     Source Verified   Fully Paid   
35               RENT    34000.00            Verified   Fully Paid   
36               RENT    22500.00            Verified  Charged Off   
...               ...         ...                 ...          ...   
395999       MORTGAGE    31789.88            Verified  Charged Off   
396015       MORTGAGE    57400.00        Not Verified   Fully Paid   
396016       MORTGAGE    70000.00     Source Verified   Fully Paid   
396021           RENT    33000.00        Not Verified   Fully Paid   
396029           RENT    42996.00            Verified   Fully Paid   

                   purpose    dti  open_acc  pub_rec  revol_bal  revol_util  \
22                   other   4.80       6.0      0.0        0.0         0.0   
25                 medical   6.56       9.0      0.0     4370.0        40.1   
32             credit_card   3.81       6.0      0.0     4912.0        13.4   
35             credit_card  26.12       9.0      1.0    14998.0        88.7   
36      debt_consolidation  18.76       7.0      0.0     7587.0        54.6   
...                    ...    ...       ...      ...        ...         ...   
395999               other  26.65       8.0      0.0    22385.0        81.0   
396015               other  14.13      12.0      0.0     3134.0         5.8   
396016      major_purchase  13.94       9.0      0.0     4062.0        12.6   
396021  debt_consolidation  21.45      18.0      0.0     3985.0         7.6   
396029  debt_consolidation   8.32       3.0      0.0     4292.0        91.3   

        total_acc application_type  mort_acc  pub_rec_bankruptcies  
22            7.0       INDIVIDUAL       NaN                   0.0  
25           10.0       INDIVIDUAL       NaN                   0.0  
32           18.0       INDIVIDUAL       NaN                   0.0  
35           20.0       INDIVIDUAL       5.0                   1.0  
36            7.0       INDIVIDUAL       0.0                   0.0  
...           ...              ...       ...                   ...  
395999       24.0       INDIVIDUAL       4.0                   0.0  
396015       27.0       INDIVIDUAL       5.0                   0.0  
396016       23.0       INDIVIDUAL       NaN                   0.0  
396021       50.0       INDIVIDUAL       NaN                   0.0  
396029       19.0       INDIVIDUAL       NaN                   0.0  

[55255 rows x 19 columns]

In [10]:
df['emp_length'].fillna(df['emp_length'].mode()[0], inplace=True)
df['revol_util'].fillna(df['revol_util'].mean(), inplace=True)
df['mort_acc'].fillna(df['mort_acc'].mean(), inplace=True)
df['pub_rec_bankruptcies'].fillna(df['pub_rec_bankruptcies'].mean(), inplace=True)


In [11]:
le = LabelEncoder() 
df['term'] = le.fit_transform(df['term'])
df['emp_length'] = le.fit_transform(df['emp_length'])
df['home_ownership'] = le.fit_transform(df['home_ownership'])
df['verification_status'] = le.fit_transform(df['verification_status'])
df['loan_status'] = le.fit_transform(df['loan_status'])
df['purpose'] = le.fit_transform(df['purpose'])
df['application_type'] = le.fit_transform(df['application_type'])


In [12]:
from scipy import stats
import numpy as np

z_score_vars = ['loan_amnt', 'int_rate', 'installment', 'annual_inc', 'dti', 'open_acc', 'pub_rec', 'revol_bal', 'revol_util', 'total_acc', 'mort_acc', 'pub_rec_bankruptcies']

for var in z_score_vars:
    z_scores = stats.zscore(df[var])
    outliers = (np.abs(z_scores) > 3)
    num_outliers = np.sum(outliers)
    print(f'Number of outliers in {var}: {num_outliers}')


Number of outliers in loan_amnt: 185
Number of outliers in int_rate: 756
Number of outliers in installment: 5050
Number of outliers in annual_inc: 3197
Number of outliers in dti: 12
Number of outliers in open_acc: 4879
Number of outliers in pub_rec: 8019
Number of outliers in revol_bal: 4790
Number of outliers in revol_util: 16
Number of outliers in total_acc: 3401
Number of outliers in mort_acc: 6843
Number of outliers in pub_rec_bankruptcies: 2325


In [13]:
z_score_vars = ['pub_rec']

for var in z_score_vars:
    z_scores = stats.zscore(df[var])
    outliers = (np.abs(z_scores) > 3)
    outlier_indices = np.where(outliers)[0]

    for index in outlier_indices:
        # Get the row of data for the outlier
        outlier_row = df.iloc[index]

        # Print or use the outlier data along with the other variables
        print(f'Outlier data in {var} at index {index}:\n{outlier_row}\n')

Outlier data in pub_rec at index 122:
loan_amnt                 8400.00
term                         0.00
int_rate                     6.92
installment                259.07
emp_length                   3.00
home_ownership               5.00
annual_inc              105000.00
verification_status          1.00
loan_status                  1.00
purpose                      1.00
dti                          6.89
open_acc                     5.00
pub_rec                      2.00
revol_bal                 6024.00
revol_util                  76.30
total_acc                   12.00
application_type             1.00
mort_acc                     1.00
pub_rec_bankruptcies         1.00
Name: 122, dtype: float64

Outlier data in pub_rec at index 134:
loan_amnt               35000.00
term                        1.00
int_rate                   19.99
installment               927.10
emp_length                  1.00
home_ownership              1.00
annual_inc              88500.00
verification_status 

In [158]:
z_score_vars = ['loan_amnt', 'int_rate', 'installment', 'annual_inc', 'dti', 'open_acc', 'pub_rec', 'revol_bal', 'total_acc']

total_entries = len(df)

for var in z_score_vars:
    z_scores = stats.zscore(df[var])
    outliers = (np.abs(z_scores) > 3)
    num_outliers = np.sum(outliers)
    percentage_outliers = (num_outliers / total_entries) * 100
    print(f'Number of outliers in {var}: {num_outliers}')
    print(f'Percentage of outliers in {var}: {percentage_outliers:.2f}%\n')

Number of outliers in loan_amnt: 185
Percentage of outliers in loan_amnt: 0.05%

Number of outliers in int_rate: 756
Percentage of outliers in int_rate: 0.19%

Number of outliers in installment: 5050
Percentage of outliers in installment: 1.28%

Number of outliers in annual_inc: 3197
Percentage of outliers in annual_inc: 0.81%

Number of outliers in dti: 12
Percentage of outliers in dti: 0.00%

Number of outliers in open_acc: 4879
Percentage of outliers in open_acc: 1.23%

Number of outliers in pub_rec: 8019
Percentage of outliers in pub_rec: 2.02%

Number of outliers in revol_bal: 4790
Percentage of outliers in revol_bal: 1.21%

Number of outliers in total_acc: 3401
Percentage of outliers in total_acc: 0.86%



In [154]:
z_score_vars = ['loan_amnt', 'int_rate', 'installment', 'annual_inc', 'dti', 'open_acc', 'pub_rec', 'revol_bal', 'revol_util', 'total_acc', 'mort_acc', 'pub_rec_bankruptcies']

total_entries = len(df)
outlier_indices = set()

for var in z_score_vars:
    z_scores = stats.zscore(df[var])
    outliers = (np.abs(z_scores) > 3)
    outlier_indices.update(np.where(outliers)[0])

num_unique_outliers = len(outlier_indices)
percentage_outliers = (num_unique_outliers / total_entries) * 100

print(f'Number of unique outliers across all variables: {num_unique_outliers}')
print(f'Percentage of unique outliers across all variables: {percentage_outliers:.2f}%')

Number of unique outliers across all variables: 26808
Percentage of unique outliers across all variables: 6.77%


In [157]:
df_info

LoanStatNew                                        Description
0              loan_amnt  The listed amount of the loan applied for by t...
1                   term  The number of payments on the loan. Values are...
2               int_rate                          Interest Rate on the loan
3            installment  The monthly payment owed by the borrower if th...
4                  grade                             LC assigned loan grade
5              sub_grade                          LC assigned loan subgrade
6              emp_title  The job title supplied by the Borrower when ap...
7             emp_length  Employment length in years. Possible values ar...
8         home_ownership  The home ownership status provided by the borr...
9             annual_inc  The self-reported annual income provided by th...
10   verification_status  Indicates if income was verified by LC, not ve...
11               issue_d                The month which the loan was funded
12           loan_status                         Current status of the loan
13               purpose  A category provided by the borrower for the lo...
14                 title            The loan title provided by the borrower
15              zip_code  The first 3 numbers of the zip code provided b...
16            addr_state  The state provided by the borrower in the loan...
17                   dti  A ratio calculated using the borrower’s total ...
18      earliest_cr_line  The month the borrower's earliest reported cre...
19              open_acc  The number of open credit lines in the borrowe...
20               pub_rec                Number of derogatory public records
21             revol_bal                     Total credit revolving balance
22            revol_util  Revolving line utilization rate, or the amount...
23             total_acc  The total number of credit lines currently in ...
24   initial_list_status  The initial listing status of the loan. Possib...
25      application_type  Indicates whether the loan is an individual ap...
26              mort_acc                       Number of mortgage accounts.
27  pub_rec_bankruptcies               Number of public record bankruptcies